In [ ]:
import time
import warnings
from pathlib import Path
from device.LaminaAdapter import LaminaAdapter
from device.LaminaAdapter import GeneratePackage_SLCP001_p4a0, GeneratePackage_SLCP101_p460, GeneratePackage_DLSY001_p460
from device.LaminaAdapter import GeneratePackage_SLCP102_p460
from device.tools.ByteConv import trans_list_to_str, trans_str_to_list

def test_communication(time_out=2):
    """ 通信成功率测试 """
    time_start = time.time()
    param_saved = dev_lamina.flag_print, dev_lamina.retry, dev_lamina.time_out
    dev_lamina.flag_print = False
    dev_lamina.retry = 1
    try:
        while True:
            dev_lamina.frame_read(0x0C, 0x20)
            print(f"Time Stamp: {time.ctime()}")
            print(f"Success Frame: {dev_lamina.log['read']}")
            print(f"Failed  Frame: {dev_lamina.log['send'] - dev_lamina.log['read']}")
            print(f"Max Series Failed Frame: {dev_lamina.log['keep-fail']}")
            time.sleep(time_out)
    finally:
        time_end = time.time()
        print("Test Result: ")
        print(f"Time Start: {time.strftime(r'%Y-%m-%d %H:%M:%S', time.localtime(time_start))}, \tTime End: {time.strftime(r'%Y-%m-%d %H:%M:%S', time.localtime(time_end))}")
        print(f"Time Elapsed: {time_end - time_start}")
        print(f"Success Rate: {dev_lamina.log['read'] / dev_lamina.log['send'] * 100}%")
        dev_lamina.flag_print, dev_lamina.retry, dev_lamina.time_out = param_saved


def make_Pakeage(fp: Path, func):
    """ 生成升级包 """

    hex_update = fp
    file_package = fp.parent / f'{hex_update.stem}.dat'
    file_update_bin = fp.parent / f'{hex_update.stem}.bin'

    data_package, data_update_bin = func(hex_update)

    file_package.write_bytes(data_package)
    file_update_bin.write_bytes(data_update_bin)

    return file_package


def test():
    if 0:
        dev_lamina.frame_read(0xA9, 1)      # 读ADC参考电压
        dev_lamina.frame_write_one(0xA9, 2000)      # 写ADC参考电压:2.0V
        dev_lamina.frame_write_one(0xA9, 3300)      # 写ADC参考电压:3.3V
        dev_lamina.frame_read(0x13, 1)      # 读输入电压
        dev_lamina.frame_read(0x16, 1)      # 读输出电压
        dev_lamina.frame_read(0x97, 4)      # 读校准参数: Vin_a, Vin_b, Vout_a, Vout_b
        dev_lamina.frame_write_one(0x97, 1000)      # 写校准参数Vin_a: 1.000
        dev_lamina.frame_write_one(0x97, 1500)      # 写校准参数Vin_a: 1.500
        dev_lamina.frame_write_one(0x98, 100)       # 写校准参数Vin_b: 1.00
        dev_lamina.frame_write_one(0x98, 150)       # 写校准参数Vin_b: 1.50
        dev_lamina.frame_write_one(0x99, 1000)      # 写校准参数Vout_a: 1.000
        dev_lamina.frame_write_one(0x99, 1500)      # 写校准参数Vout_a: 1.500
        dev_lamina.frame_write_one(0x9A, 1000)      # 写校准参数Vout_a: 1.00
        dev_lamina.frame_write_one(0x9A, 1500)      # 写校准参数Vout_a: 1.50
    if 0:
        dev_lamina.frame_write_str(0x82, [0xAA, 0xAA, 0xAA, 0xAA, 0xAA, 0xAA])
        dev_lamina.frame_write_str(0x82, [0x00, 0x00, 0x00, 0x00, 0x00, 0x00])
        dev_lamina.frame_write_str(0x82, [0x0A, 0x00, 0x00, 0x00, 0x00, 0x00])
        dev_lamina.frame_write_str(0x82, [0xFF, 0x00, 0x00, 0x00, 0x00, 0x00])
        dev_lamina.frame_write_str(0x82, [0xA1, 0x00, 0x00, 0x00, 0x00, 0x00])
        dev_lamina.frame_write_str(0x82, [0x1A, 0x00, 0x00, 0x00, 0x00, 0x00])
        dev_lamina.frame_write_str(0x82, [0x99, 0x99, 0x99, 0x99, 0x99, 0x99])
        dev_lamina.frame_write_str(0x82, [0x00, 0x00, 0x00, 0x00, 0x00, 0x01])
    if 0:
        dev_lamina.frame_write_one(0x52, 0x01)
        time.sleep(0.5)
        dev_lamina.frame_write_one(0x50, 0x00)
    if 0:
        while 1:
            code_mes = input("扫描数据")
            temp = code_mes[5:7] + code_mes[-10:]
            code_addr = [int(temp[i:i+2], 16) for i in range(0, len(temp), 2)]
            print(f"扫描结果: {code_mes}")
            print(f"载波地址: {trans_list_to_str(code_addr)}")
            dev_lamina.frame_read(0x100, 0x20)
            time.sleep(0.5)
            dev_lamina.frame_write_str(0x0180, list(code_mes))
            time.sleep(0.5)
            dev_lamina.frame_read(0x180, 0x10)
            time.sleep(0.5)
            dev_lamina.frame_write_str(0x82, code_addr)
            time.sleep(0.5)
            dev_lamina.frame_read(0x80, 0x08)
            time.sleep(0.5)
            dev_lamina.frame_write_one(0xA3, 0x01)
            time.sleep(0.5)
            dev_lamina.frame_write_one(0x51, 0x01)
            time.sleep(5)
            dev_lamina.frame_read(0x0E, 0x13)
            time.sleep(5)
            dev_lamina.frame_read(0x0E, 0x13)
            time.sleep(0.5)
            dev_lamina.frame_write_one(0x50, 0x00)
    if 0:
        dev_lamina.frame_write_one(0x0054, 0x01)
        dev_lamina.frame_read(0x000E, 0x02)
        dev_lamina.frame_write_one(0x0054, 0x03)
        dev_lamina.frame_read(0x000E, 0x02)
        dev_lamina.frame_write_one(0x0054, 0x07)
        dev_lamina.frame_read(0x000E, 0x02)
        dev_lamina.frame_write_one(0x0054, 0x06)
        dev_lamina.frame_read(0x000E, 0x02)
        dev_lamina.frame_write_one(0x0054, 0x04)
        dev_lamina.frame_read(0x000E, 0x02)
        dev_lamina.frame_write_one(0x0054, 0x00)
        dev_lamina.frame_read(0x000E, 0x02)
    if 0:
        dev_lamina.frame_read(0x0E, 0x14)
    if 0:
        dev_lamina.frame_read(0x60, 0x60)
    if 0:
        dev_lamina.frame_read(0x70, 0x02)
        dev_lamina.frame_write_one(0x70, 2100)
        dev_lamina.frame_write_one(0x71, 2200)
        dev_lamina.frame_read(0x70, 0x02)
        dev_lamina.frame_write_one(0x70, 2300)
        dev_lamina.frame_write_one(0x71, 2100)
        dev_lamina.frame_read(0x70, 0x02)
    if 0:
        dev_lamina.frame_write_str(0x0170, list("SN202405201117-1"))
        dev_lamina.frame_write_str(0x0180, list("MES202405201117-2"))
        dev_lamina.frame_write_str(0x0190, list("D202405211500-3"))
        time.sleep(2)
        dev_lamina.frame_read(0x0170, 0x30)

    if 0:
        dev_lamina.flag_print = False
        dev_lamina.frame_write_one(0x52, 0x01)
        time.sleep(6)
        dev_lamina.frame_read(0x69, 0x02)
        for value in [40, 41.9, 42, 42.1, 56.5, 57, 57.5, 57.9, 58, 58.1, 59]:
            time.sleep(0.5)
            result = dev_lamina.frame_write_one(0x21, int(value * 10))
            print(f"Write Value: {value}, result: {'Seccusss' if result else 'Fail'}.")
            time.sleep(0.5)
            dev_lamina.frame_read(0x21,1)
        time.sleep(0.5)
        value = 46
        result = dev_lamina.frame_write_one(0x69, int(value * 10))
        print(f"Write Value: {value} in Addr: {0x69}, result: {'Seccusss' if result else 'Fail'}.")
        time.sleep(0.5)
        value = 60
        result = dev_lamina.frame_write_one(0x6A, int(value * 10))
        print(f"Write Value: {value} in Addr: {0x6A}, result: {'Seccusss' if result else 'Fail'}.")
        for value in [45, 45.9, 46, 46.1, 56.5, 57, 57.5, 58, 59.9, 60, 60.1, 61]:
            time.sleep(0.5)
            result = dev_lamina.frame_write_one(0x21, int(value * 10))
            print(f"Write Value: {value}, result: {'Seccusss' if result else 'Fail'}.")
            time.sleep(0.5)
            dev_lamina.frame_read(0x21,1)
        time.sleep(0.5)
        dev_lamina.frame_write_one(0x53, 0x01)
        time.sleep(4.5)
        dev_lamina.frame_read(0x21, 1)
        time.sleep(0.5)
        dev_lamina.frame_read(0x69, 2)
        dev_lamina.flag_print = True

    if 0:   # 并机功率限值测试
        dev_lamina.flag_print = False
        step = 0
        time_start = time.time()
        time_interval = 120
        list_power_limit = [650, 300, 200, 150, 120, 100, 80, 70, 50, 25, 10, 5, 1, 0.1, 0, 650]
        while True:
            time.sleep(1)
            print(time.ctime())
            dev_lamina.frame_read(0x0E, 0x20)
            if time.time() - time_start > time_interval:
                if step >= len(list_power_limit):
                    break
                time.sleep(0.5)
                time_start = time.time()
                value = list_power_limit[step]
                result = dev_lamina.frame_write_dual(0x1F, int(value * 1000))
                print(f"Write Value: {value} in Addr: 0x1F by Time: {time.ctime(time_start)}. \n\tresult: {'Seccusss' if result else 'Fail'}.")
                step += 1
        dev_lamina.flag_print = True
    if 0:   # 启停机条件测试
        dev_lamina.flag_print = False
        dev_lamina.frame_read(0x60, 0x0B)        
        while True:
            time.sleep(1)
            print(time.ctime())
            dev_lamina.frame_read(0x0E, 0x20)
        dev_lamina.flag_print = True

if __name__=='__main__':
    mode_config = {
        "Log": {'com_name': None, 
                # 'addr_645': [0x01, 0x00, 0x00, 0x00, 0x00, 0x40], 
                },
        "Debug": {'com_name': 'COM3', 'baudrate': 115200, 'parity': 'N', 'bytesize': 8, 'stopbits': 1,
                #   'addr_645': [0x01, 0x02, 0x03, 0x04, 0x05, 0x06], 
                  'frame_print': True, 
                  'time_out': 0.5, 'retry': 1, 'retry_sub': 10},
        "HPLC":  {'com_name': 'COM9', 'baudrate': 9600, 'parity': 'E', 'bytesize': 8, 'stopbits': 1,
                  'addr_645': trans_str_to_list("02 01 00 00 24 20"), 
                  'frame_print': True, 
                  'time_out': 3, 'time_gap': 0.1, 'retry': 3, 'retry_sub': 10},
    }

    dev_lamina = LaminaAdapter(type_dev="SLCP102", **mode_config['Debug'])

    dev_lamina.frame_read(0x0100, 0x20)
    # dev_lamina.frame_write_one(0x51, 0x01)
    # dev_lamina.frame_read(0x1A0, 0x20)
    # dev_lamina.frame_log()
    # dev_lamina.frame_read(0x1A0, 0x20)

    # 工程-即时转换
    if dev_lamina.device == 'SLCP001':
        file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V1\lamina_adapter\Debug\lamina_adapter.hex")
    elif dev_lamina.device == 'SLCP101':
        file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V3.01\lamina_adapter\Debug\lamina_adapter.hex")
        # file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V2.03\lamina_adapter\Debug\lamina_adapter.hex")
    elif dev_lamina.device == 'SLCP102':
        file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V3.01\lamina_adapter\Debug\lamina_adapter.hex")
    elif dev_lamina.device == 'DLSY001':
        file_hex = Path(r"D:\WorkingProject\LightStackOptimizer\software\lamina_optimizer\lamina_optimizer\Debug\lamina_optimizer.hex")
    else:
        file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\lamina_adapter\Debug\lamina_adapter.hex")
    if not file_hex.exists():
        raise Exception("工程编译目标文件不存在.")
    if dev_lamina.output['Regs'][0x100][1].split('_')[0] != dev_lamina.device:
        warnings.warn("设备型号不匹配.", UserWarning)
    print(dev_lamina.device)
    print(file_hex)

    if not hasattr(__builtins__,"__IPYTHON__"):
        version = "SLCP101_241030_2000_V2.03"
        addr = [0x24, 0x09, 0x12, 0x00, 0x00, 0x00]

        while True:
            """ 自动检测升级流程 """
            ret = False
            while not ret or ('Regs' not in dev_lamina.output.keys()) or (version == dev_lamina.output['Regs'][0x0100][1].strip('\000')):
                # dev_lamina.frame_read(0x82, 3)
                ret = dev_lamina.frame_read(0x0100, 0x20)
                time.sleep(1)

            dev_lamina.frame_update(file_hex, makefile=True)

            time.sleep(3)

            ret = dev_lamina.frame_read(0x0100, 0x20)

            if ret and (version == dev_lamina.output['Regs'][0x0100][1]):
                dev_lamina.frame_write_one(0x52, 0x01)

                # print(f"address: {' '.join(map(lambda x: ('000' + hex(x)[2:])[-2:], addr))}")
                # dev_lamina.frame_write_str(0x82, addr)
                # dev_lamina.frame_read(0x82, 3)
                # addr[5] += 1
                # if addr[5] & 0x0F >= 10:
                #     addr[5] += 0x10 - 10

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 01 00 00 20 45 EE 4B 16
Read Frame:  68 01 02 03 04 05 06 68 9F 45 01 03 40 4C 53 50 43 30 31 5F 32 34 32 31 31 37 32 31 5F 30 37 5F 30 33 56 30 2E 00 31 00 00 00 00 00 00 56 50 2D 43 38 34 37 2D 30 30 44 2D 00 58 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 BC 16 E1 16
Parse Result:
0x0100: SLCP102_241127_1700_V3.01        版本(ODM)
0x0110: PVC-48-700-DX                    型号     
SLCP102
D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V3.01\lamina_adapter\Debug\lamina_adapter.hex


In [ ]:
dev_lamina.frame_read(0x60, 0x60)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 60 00 60 45 FC F8 16
Read Frame:  68 01 02 03 04 05 06 68 9F C5 01 03 C0 00 01 00 78 02 62 00 5A 02 6C 00 64 02 1C 01 CC 02 3A 01 A4 02 44 02 94 02 58 01 B8 09 60 07 D0 00 0A 08 98 02 3A 02 35 02 21 04 1A 03 B6 03 52 01 5E 02 30 AE 60 00 0A 03 E8 00 00 EB 10 00 09 EB 10 00 09 05 06 03 04 01 02 09 C4 FE 0C 00 64 00 00 00 64 00 0D 03 96 00 96 C3 50 00 00 00 C8 00 00 00 FA 00 00 00 14 00 00 00 02 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 00 00 00 00 00 00 03 E8 37 E2 2D BD 02 23 00 01 0C AD FF FF FF FF FF FF FF FF FF FF FF FF 4C 53 50 43 30 31 5F 32 34 32 31 31 37 32 31 5F 30 37 5F 30 33 56 30 2E 00 31 00 00 00 00 00 00 2C F5 60 16
Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0         

True

In [ ]:
dev_lamina.frame_update(file_hex, makefile=True)
time.sleep(4.5)
dev_lamina.frame_read(0x100, 0x20)

Package generated successfully.
File name: lamina_adapter.hex
File Info:
	 header_length=184, bin_length=132178[0x20452]


File Transmitting: 100%|██████████| 612/612 [00:28<00:00, 21.10it/s]


Discard Data:  b'MICRO MONITOR 1.20.13\r\nPlatform: HC32F460\r\nCPU: HC32F460\r\nBuilt: Nov  1 2024 @ 15:04:03\r\nMonitor RAM: 0x1fff8448-0x1fff938c\r\nApplication RAM Base: 0x20010000\r\nst:aa,bb,wk:ffffffff,bs:ffff,cnt:ffff\r\ncd:ffffffff,ffffffff\r\ncd_w:ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff,ff\r\nbk:53504f54,4d4d4f43\r\nbk:45,0,53,4c,43,50,31,30,32,0,0,0,0,0,1,0\r\nstate:0\r\ns_boot\r\nf_size:20452, f_md5:98,1d,c7,66,bc,d3,f6,fd,d4,1a,7a,55,7f,61,f0,84\r\nb_rl md5:98,1d,c7,66,bc,d3,f6,fd,d4,1a,7a,55,7f,61,f0,84\r\nc000, 20010000, 8192, d-1\r\ne000, 20012000, 8192, d-1\r\n10000, 20014000, 8192, d-1\r\n12000, 20016000, 8192, d-1\r\n14000, 20010000, 8192, d-1\r\n16000, 20012000, 8192, d-1\r\n18000, 20014000, 8192, d-1\r\n1a000, 20016000, 8192, d-1\r\n1c000, 20010000, 8192, d-1\r\n1e000, 20012000, 8192, d-1\r\n20000, 20014000, 8192, d-1\r\n22000, 20016000, 8192, d-1\r\n24000, 20010000, 8192, d-1\r\n26000, 20012000, 8192, d-1\r\n28000, 20014000, 8192, d-1\r\n2a000, 20016000, 8192

True

In [ ]:
dev_lamina.frame_read(0x0E, 0x20)

Discard Data:  b'MICRO MONITOR 1.20.13\r\nPlatform: HC32F460\r\nCPU: HC32F460\r\nBuilt: Nov  1 2024 @ 15:04:03\r\nMonitor RAM: 0x1fff8448-0x1fff938c\r\nApplication RAM Base: 0x20010000\r\njump to app...\r\r\n'
Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Read Frame:  68 01 02 03 04 05 06 68 9F 2D 01 03 28 00 00 00 01 00 00 00 00 00 00 00 35 00 00 00 71 02 14 00 00 01 03 01 0B 00 00 00 00 01 0B 00 00 02 1C EB 10 00 09 02 35 1C 67 92 16
Parse Result:
0x000E: 0x0000 故障字1     
0x000F: 0x0001 故障字2     
0x0010: 0x0000 MPPT工作状态 
0x0011: 0x0000 系统工作状态   
0x0012: 0x0000 系统工作模式   
0x0013: 5.3    输入电压     
0x0014: 0.0    电感电流     
0x0015: 11.3   12V电压    
0x0016: 53.2   输出电压     
0x0017: 0.0    输入电流     
0x0018: 25.9   温度1      
0x0019: 26.7   温度2      
0x001A: 0.0    输入功率     
0x001C: 26.7   设备温度     
0x001D: 0x0000 开关机状态    
0x001E: 54.0   电池电压     
0x001F: 650.0  并机功率限值   
0x0021: 56.5   输出限功率电压阈值


True

In [ ]:
dev_lamina.frame_read(0x60, 0x60)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 60 00 60 45 FC F8 16
Read Frame:  68 01 02 03 04 05 06 68 9F C5 01 03 C0 00 01 00 78 02 62 00 5A 02 6C 00 64 02 1C 01 CC 02 3A 01 A4 02 44 02 94 02 58 01 B8 09 60 07 D0 00 0A 08 98 02 3A 02 35 02 21 04 1A 03 B6 03 52 01 5E 02 30 AE 60 00 0A 03 E8 00 00 EB 10 00 09 EB 10 00 09 05 06 03 04 01 02 09 C4 FE 0C 00 64 00 00 00 64 00 0D 03 96 00 96 C3 50 00 00 00 C8 00 00 00 FA 00 00 00 14 00 00 00 02 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 00 00 00 00 00 00 03 E8 37 DC 2D B4 02 23 00 01 0C AD 01 FF FF FF FF FF FF FF FF FF FF FF 4C 53 50 43 30 31 5F 32 35 32 31 30 33 31 30 5F 33 38 5F 30 33 56 30 2E 61 31 00 32 00 00 00 00 48 FE 09 16
Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0         

True

In [ ]:
f"{0x120:h}"

ValueError: Unknown format code 'h' for object of type 'int'

In [ ]:
f"{0x120:x}"

'120'

In [ ]:
f"{0x120:0xx}"

ValueError: Invalid format specifier '0xx' for object of type 'int'

In [ ]:
f"0x{120:x}"

'0x78'

In [ ]:
f"0x{0x120:x}"

'0x120'

In [ ]:
dev_lamina.flag_print = False
action_list = [(0x50, 0), (0x50, 1), (0x50, 0), (0xA8, 0), (0x50, 1)]
dev_lamina.frame_write_one(0x52, 1)        
time.sleep(4.5)
dev_lamina.frame_read(0x60, 0x60)
step = 0
time_start = time.time()
time_interval = 120
while True:
    time.sleep(1)
    print(time.ctime())
    dev_lamina.frame_read(0x0E, 0x20)
    if time.time() - time_start > time_interval:
        if step >= len(list_power_limit):
            break
        time.sleep(0.5)
        time_start = time.time()
        result = dev_lamina.frame_write_one(*action_list[step])
        print(f"Write Value: {action_list[step][1]} in Addr: 0x{action_list[step][0]:x} by Time: {time.ctime(time_start)}. \n\tresult: {'Seccusss' if result else 'Fail'}.")
        step += 1
dev_lamina.flag_print = True

Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0                             最大停止输入电压             
0x0065: 10.0                             最小MPPT电压             
0x0066: 54.0                             最大MPPT电压             
0x0067: 46.0                             最小启动输出电压             
0x0068: 57.0                             最大启动输出电压             
0x0069: 42.0                             最小停止输出电压             
0x006A: 58.0                             最大停止输出电压             
0x006B: 66.0                             输入过压保护值              
0x006C: 60.0                             输出过压保护值              
0x006D: 44.0                             输出欠压保护值              
0x006E: 24.0                             电感过流保护值              
0x006F: 20.0                             

NameError: name 'list_power_limit' is not defined

In [ ]:
dev_lamina.flag_print = False
action_list = [(0x50, 0), (0x50, 1), (0x50, 0), (0xA8, 0), (0x50, 1)]
dev_lamina.frame_write_one(0x50, 0)
time.sleep(0.5)
dev_lamina.frame_write_one(0x52, 1)        
time.sleep(4.5)
dev_lamina.frame_read(0x60, 0x60)
step = 0
time_start = time.time()
time_interval = 120
while True:
    time.sleep(1)
    print(time.ctime())
    dev_lamina.frame_read(0x0E, 0x20)
    if time.time() - time_start > time_interval:
        if step >= len(action_list):
            break
        time.sleep(0.5)
        time_start = time.time()
        result = dev_lamina.frame_write_one(*action_list[step])
        print(f"Write Value: {action_list[step][1]} in Addr: 0x{action_list[step][0]:x} by Time: {time.ctime(time_start)}. \n\tresult: {'Seccusss' if result else 'Fail'}.")
        step += 1
dev_lamina.flag_print = True

Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0                             最大停止输入电压             
0x0065: 10.0                             最小MPPT电压             
0x0066: 54.0                             最大MPPT电压             
0x0067: 46.0                             最小启动输出电压             
0x0068: 57.0                             最大启动输出电压             
0x0069: 42.0                             最小停止输出电压             
0x006A: 58.0                             最大停止输出电压             
0x006B: 66.0                             输入过压保护值              
0x006C: 60.0                             输出过压保护值              
0x006D: 44.0                             输出欠压保护值              
0x006E: 24.0                             电感过流保护值              
0x006F: 20.0                             

In [ ]:
dev_lamina.flag_print = False
action_list = [(0x50, 0), (0xA8, 0), (0x50, 1)]
dev_lamina.frame_write_one(0x50, 0)
time.sleep(0.5)
dev_lamina.frame_write_one(0x52, 1)        
time.sleep(4.5)
dev_lamina.frame_read(0x60, 0x60)
step = 0
time_start = time.time()
time_interval = 120
while True:
    time.sleep(1)
    print(time.ctime())
    dev_lamina.frame_read(0x0E, 0x20)
    if time.time() - time_start > time_interval:
        if step >= len(action_list):
            break
        time.sleep(0.5)
        time_start = time.time()
        result = dev_lamina.frame_write_one(*action_list[step])
        print(f"Write Value: {action_list[step][1]} in Addr: 0x{action_list[step][0]:x} by Time: {time.ctime(time_start)}. \n\tresult: {'Seccusss' if result else 'Fail'}.")
        step += 1
dev_lamina.flag_print = True

Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0                             最大停止输入电压             
0x0065: 10.0                             最小MPPT电压             
0x0066: 54.0                             最大MPPT电压             
0x0067: 46.0                             最小启动输出电压             
0x0068: 57.0                             最大启动输出电压             
0x0069: 42.0                             最小停止输出电压             
0x006A: 58.0                             最大停止输出电压             
0x006B: 66.0                             输入过压保护值              
0x006C: 60.0                             输出过压保护值              
0x006D: 44.0                             输出欠压保护值              
0x006E: 24.0                             电感过流保护值              
0x006F: 20.0                             

In [ ]:
dev_lamina.flag_print = False
action_list = [(0x50, 0), (0xA8, 0), (0x50, 1)]
dev_lamina.frame_write_one(0x50, 0)
time.sleep(0.5)
dev_lamina.frame_write_one(0x52, 1)        
time.sleep(4.5)
dev_lamina.frame_read(0x60, 0x60)
step = 0
time_start = time.time()
time_interval = 120
while True:
    time.sleep(1)
    print(time.ctime())
    dev_lamina.frame_read(0x0E, 0x20)
    if time.time() - time_start > time_interval:
        if step >= len(action_list):
            break
        time.sleep(0.5)
        time_start = time.time()
        result = dev_lamina.frame_write_one(*action_list[step])
        print(f"Write Value: {action_list[step][1]} in Addr: 0x{action_list[step][0]:x} by Time: {time.ctime(time_start)}. \n\tresult: {'Seccusss' if result else 'Fail'}.")
        step += 1
dev_lamina.flag_print = True

Parse Result:
0x0060: 0x0001                           光伏通道使能               
0x0061: 12.0                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0                             最大停止输入电压             
0x0065: 10.0                             最小MPPT电压             
0x0066: 54.0                             最大MPPT电压             
0x0067: 46.0                             最小启动输出电压             
0x0068: 57.0                             最大启动输出电压             
0x0069: 42.0                             最小停止输出电压             
0x006A: 58.0                             最大停止输出电压             
0x006B: 66.0                             输入过压保护值              
0x006C: 60.0                             输出过压保护值              
0x006D: 44.0                             输出欠压保护值              
0x006E: 24.0                             电感过流保护值              
0x006F: 20.0                             